In [1]:
from langchain_community.agent_toolkits import create_sql_agent
from langchain_openai import ChatOpenAI
from langchain_groq import ChatGroq
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.pydantic_v1 import BaseModel, Field
import pandas as pd
from pydantic import BaseModel, Field

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser


gpt = ChatOpenAI(model="gpt-3.5-turbo", temperature=0)
#agent_gpt_executor = create_sql_agent(gpt, db=db, agent_type="tool-calling", verbose=True)

## make database
from langchain_community.utilities import SQLDatabase
from sqlalchemy import create_engine

from langchain.prompts import ChatPromptTemplate
from langchain.schema import SystemMessage
from langchain_core.prompts import MessagesPlaceholder
#agent_groq_executor = create_sql_agent(llm, db=db, agent_type="tool-calling", verbose=True)

from OpenAITools.FetchTools import fetch_clinical_trials, fetch_clinical_trials_jp
from OpenAITools.CrinicalTrialTools import QuestionModifierEnglish, TumorNameExtractor, SimpleClinicalTrialAgent,GraderAgent,LLMTranslator


/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/IPython/core/interactiveshell.py:3577: LangChainDeprecationWarning: As of langchain-core 0.3.0, LangChain uses pydantic v2 internally. The langchain_core.pydantic_v1 module was a compatibility shim for pydantic v1, and should no longer be used. Please update the code to import from Pydantic directly.

For example, replace imports like: `from langchain_core.pydantic_v1 import BaseModel`
with: `from pydantic import BaseModel`
or the v1 compatibility namespace if you are working in a code base that has not been fully upgraded to pydantic 2 yet. 	from pydantic.v1 import BaseModel

  exec(code_obj, self.user_global_ns, self.user_ns)


#### Define LLMS

In [2]:
gpt = ChatOpenAI(model="gpt-3.5-turbo", temperature=0)
#agent_gpt_executor = create_sql_agent(gpt, db=db, agent_type="tool-calling", verbose=True)
groq = ChatGroq(model_name="llama3-70b-8192", temperature=0)
#agent_groq_executor = create_sql_agent(groq, db=db, agent_type="tool-calling", verbose=True)

In [3]:
age = "65"
sex ="男性"
tumor_type ="胃癌"
#tumor_type = "gastric cancer"
GeneMutation ="HER2"
Meseable = "有り"
Biopsiable = "有り"
NCTID = 'NCT06441994'


In [4]:
def generate_ex_question(age, sex, tumor_type, GeneMutation, Meseable, Biopsiable):
    # GeneMutationが空の場合はUnknownに設定
    gene_mutation_text = GeneMutation if GeneMutation else "Unknown"
    
    # MeseableとBiopsiableの値をYes, No, Unknownに変換
    meseable_text = (
        "Yes" if Meseable == "有り" else "No" if Meseable == "無し" else "Unknown"
    )
    biopsiable_text = (
        "Yes" if Biopsiable == "有り" else "No" if Biopsiable == "無し" else "Unknown"
    )
    
    # 質問文の生成
    ex_question = f"""{age}歳{sex}の{tumor_type}患者さんはこの治験に参加することができますか？
判明している遺伝子変異: {gene_mutation_text}
Meseable tumor: {meseable_text}
Biopsiable tumor: {biopsiable_text}
です。
"""
    return ex_question

In [5]:
def generate_ex_question_English(age, sex, tumor_type, GeneMutation, Meseable, Biopsiable):
    # GeneMutationが空の場合は"Unknown"に設定
    gene_mutation_text = GeneMutation if GeneMutation else "Unknown"
    
    # sexの値を male または female に変換
    sex_text = "male" if sex == "男性" else "female" if sex == "女性" else "Unknown"
    
    # MeseableとBiopsiableの値を "Yes", "No", "Unknown" に変換
    meseable_text = (
        "Yes" if Meseable == "有り" else "No" if Meseable == "無し" else "Unknown"
    )
    biopsiable_text = (
        "Yes" if Biopsiable == "有り" else "No" if Biopsiable == "無し" else "Unknown"
    )
    
    # 英語での質問文を生成
    ex_question = f"""Can a {age}-year-old {sex_text} patient with {tumor_type} participate in this clinical trial?
Known gene mutation: {gene_mutation_text}
Measurable tumor: {meseable_text}
Biopsiable tumor: {biopsiable_text}
"""
    return ex_question


In [6]:
#Define extractor
Translator = LLMTranslator(groq)
TumorName = Translator.translate(tumor_type)
print(TumorName)

Stomach cancer


In [7]:
TumorName = "gastric cancer"

In [8]:
ex_question = generate_ex_question_English(age, sex, TumorName, GeneMutation, Meseable, Biopsiable)
ex_question

'Can a 65-year-old male patient with gastric cancer participate in this clinical trial?\nKnown gene mutation: HER2\nMeasurable tumor: Yes\nBiopsiable tumor: Yes\n'

ex_question = """"65歳男性の胃癌患者さんはこの治験に参加することができますか？
判明している遺伝子変異:HER2
Meseable tumor:Yes
biopsiable tumor: Yes
です。
"""

In [9]:
#ex_question = "65歳男性でが参加できる臨床治験を教えて下さい。"

In [10]:
#ex_question = "65歳男性でBRCA遺伝子の変異がある前立患者さんが参加できる臨床治験を教えて下さい。"

modifierEnglish = QuestionModifierEnglish(groq)
modifierEnglish.modify_question(ex_question)

In [11]:
#Make db
df = fetch_clinical_trials(TumorName)
# 新しい列を追加
df['AgentJudgment'] = None
df['AgentGrade'] = None
#df = df.iloc[:5, :]
NCTIDs = list(df['NCTID' ])


Fetching data from: https://clinicaltrials.gov/api/v2/studies?query.titles=gastric cancer SEARCH[Location](AREA[LocationCountry]Japan AND AREA[LocationStatus]Recruiting)&pageSize=100


In [12]:
df

NCTID                                              Title  \
0   NCT03505320  A Study of Zolbetuximab (IMAB362) in Adults Wi...   
1   NCT05002127  A Study of Evorpacept (ALX148) in Patients wit...   
2   NCT05365581  A Study of ASP2138 Given by Itself or Given Wi...   
3   NCT05111626  Bemarituzumab Plus Chemotherapy and Nivolumab ...   
4   NCT06324357  Beamion BCGC-1: A Study to Find a Suitable Dos...   
5   NCT06056024  A Study to Test How Well Different Doses of BI...   
6   NCT04379596  Ph1b/2 Study of the Safety and Efficacy of T-D...   
7   NCT00197470    Cytokine Gene Polymorphisms in Gastric Diseases   
8   NCT05205343  Trans-Pacific Multicenter Collaborative Study ...   
9   NCT06490055  Predicting the Efficacy in Advanced Gastric Ca...   
10  NCT06490159  Predicting Peripheral Neuropathy of Paclitaxel...   
11  NCT05438459  GAIA-102 Intraperitoneal Administration in Pat...   
12  NCT04745988  An Open Label Phase 2 Study to Evaluate the Sa...   
13  NCT06038578  A Study of TRK-950 When Used in Combination Wi...   
14  NCT05322577  A Study Evaluating Bemarituzumab in Combinatio...   
15  NCT05152147  A Study of Zanidatamab in Combination With Che...   

   Primary Completion Date                                             Cancer  \
0               2025-04-30  Pharmacokinetics of Zolbetuximab, Gastric Canc...   
1                  2026-07  Gastric Cancer, Gastroesophageal Junction Aden...   
2               2026-10-31  Gastric Adenocarcinoma, Gastroesophageal Junct...   
3               2026-09-26  Gastric Cancer, Gastroesophageal Junction Aden...   
4               2027-02-22  Metastatic Breast Cancer, Metastatic Gastric A...   
5               2027-05-26                         Solid Tumor, KRAS Mutation   
6               2026-07-30                                     Gastric Cancer   
7             Unknown Date      Gastric Ulcer, Duodenal Ulcer, Gastric Cancer   
8               2026-05-31      Gastrostomy, Gastric, GastroEsophageal Cancer   
9               2025-12-31  Gastric Cancer, Chemotherapy Effect, Paclitaxe...   
10              2025-12-31  Gastric Cancer, Chemotherapy-induced Periphera...   
11              2026-12-31                  Gastric Cancer, Pancreatic Cancer   
12                 2025-08                                     Gastric Cancer   
13              2025-08-31  Gastric Adenocarcinoma, Gastric Cancer, Gastro...   
14              2026-03-17   Gastric Cancer, Gastroesophageal Junction Cancer   
15              2024-12-31  Gastric Neoplasms, Gastroesophageal Adenocarci...   

                                              Summary  \
0   Zolbetuximab is being studied as a treatment f...   
1   A Phase 2/3 Study of Evorpacept (ALX148) in Co...   
2   Claudin 18.2 protein, or CLDN18.2 is a protein...   
3   The main objective of Part 1 is to evaluate th...   
4   This study is open to adults aged 18 years and...   
5   This study is open to adults with advanced can...   
6   DESTINY-Gastric03 will investigate the safety,...   
7   Recently, cytokine polymorphisms are considere...   
8   To compare the symptoms of patients who have a...   
9   With advances in chemotherapy for gastric canc...   
10  Although advances in chemotherapy have improve...   
11  Phase I Part :\n\nConfirm the safety of GAIA-1...   
12  This study is an open label phase 2 study to e...   
13  This study will assess the efficacy, safety, o...   
14  The main objectives of this study are to evalu...   
15  This study is being done to find out if zanida...   

                                    Japanes Locations  \
0                                        Chiba, Tokyo   
1   Chiba, Fukuoka, Gifu, Kumamoto, Kyoto, Nagasak...   
2   Kashiwa, Nagoya, Osakasayama, Suita, Yokohama, ku   
3                               Sapporo, gun, ku, shi   
4                                             ku, shi   
5                                         Kashiwa, ku   
6                               Kashiwa, gun, ku, shi   
7              

In [13]:

#Define agents
#modifier = QuestionModifierEnglish(groq)
CriteriaCheckAgent = SimpleClinicalTrialAgent(groq)
grader_agent = GraderAgent(groq)

In [14]:
for nct_id in NCTIDs:
    TargetCriteria = df.loc[df['NCTID'] == nct_id, 'Eligibility Criteria'].values[0]
    AgentJudgment = CriteriaCheckAgent.evaluate_eligibility(TargetCriteria, ex_question)
    print(AgentJudgment)

    AgentGrade = grader_agent.evaluate_eligibility(AgentJudgment)
    print(AgentGrade)
    # NCTIDに一致する行を見つけて更新
    df.loc[df['NCTID'] == nct_id, 'AgentJudgment'] = AgentJudgment
    df.loc[df['NCTID'] == nct_id, 'AgentGrade'] = AgentGrade


The patient is not eligible for this clinical trial because the inclusion criteria specify that female subjects are eligible, and the patient is a 65-year-old male.
no
The patient is eligible for this clinical trial based on the provided information, as he has a measurable and biopsiable tumor with a known HER2 gene mutation, which meets the inclusion criteria. However, I do not know if he has progressed on or after a prior HER2-directed agent and fluoropyrimidine- or platinum-containing chemotherapy, which is also required for inclusion.
unclear
The patient is eligible for this clinical trial based on the provided criteria. The patient meets the inclusion criteria, including having a measurable tumor, being at least 18 years old, and having a predicted life expectancy of at least 12 weeks. The patient also has histologically confirmed gastric/gastroesophageal junction (GEJ) adenocarcinoma, which is one of the specified disease types for this trial. Additionally, the patient has a HER2

In [15]:
df

NCTID                                              Title  \
0   NCT03505320  A Study of Zolbetuximab (IMAB362) in Adults Wi...   
1   NCT05002127  A Study of Evorpacept (ALX148) in Patients wit...   
2   NCT05365581  A Study of ASP2138 Given by Itself or Given Wi...   
3   NCT05111626  Bemarituzumab Plus Chemotherapy and Nivolumab ...   
4   NCT06324357  Beamion BCGC-1: A Study to Find a Suitable Dos...   
5   NCT06056024  A Study to Test How Well Different Doses of BI...   
6   NCT04379596  Ph1b/2 Study of the Safety and Efficacy of T-D...   
7   NCT00197470    Cytokine Gene Polymorphisms in Gastric Diseases   
8   NCT05205343  Trans-Pacific Multicenter Collaborative Study ...   
9   NCT06490055  Predicting the Efficacy in Advanced Gastric Ca...   
10  NCT06490159  Predicting Peripheral Neuropathy of Paclitaxel...   
11  NCT05438459  GAIA-102 Intraperitoneal Administration in Pat...   
12  NCT04745988  An Open Label Phase 2 Study to Evaluate the Sa...   
13  NCT06038578  A Study of TRK-950 When Used in Combination Wi...   
14  NCT05322577  A Study Evaluating Bemarituzumab in Combinatio...   
15  NCT05152147  A Study of Zanidatamab in Combination With Che...   

   Primary Completion Date                                             Cancer  \
0               2025-04-30  Pharmacokinetics of Zolbetuximab, Gastric Canc...   
1                  2026-07  Gastric Cancer, Gastroesophageal Junction Aden...   
2               2026-10-31  Gastric Adenocarcinoma, Gastroesophageal Junct...   
3               2026-09-26  Gastric Cancer, Gastroesophageal Junction Aden...   
4               2027-02-22  Metastatic Breast Cancer, Metastatic Gastric A...   
5               2027-05-26                         Solid Tumor, KRAS Mutation   
6               2026-07-30                                     Gastric Cancer   
7             Unknown Date      Gastric Ulcer, Duodenal Ulcer, Gastric Cancer   
8               2026-05-31      Gastrostomy, Gastric, GastroEsophageal Cancer   
9               2025-12-31  Gastric Cancer, Chemotherapy Effect, Paclitaxe...   
10              2025-12-31  Gastric Cancer, Chemotherapy-induced Periphera...   
11              2026-12-31                  Gastric Cancer, Pancreatic Cancer   
12                 2025-08                                     Gastric Cancer   
13              2025-08-31  Gastric Adenocarcinoma, Gastric Cancer, Gastro...   
14              2026-03-17   Gastric Cancer, Gastroesophageal Junction Cancer   
15              2024-12-31  Gastric Neoplasms, Gastroesophageal Adenocarci...   

                                              Summary  \
0   Zolbetuximab is being studied as a treatment f...   
1   A Phase 2/3 Study of Evorpacept (ALX148) in Co...   
2   Claudin 18.2 protein, or CLDN18.2 is a protein...   
3   The main objective of Part 1 is to evaluate th...   
4   This study is open to adults aged 18 years and...   
5   This study is open to adults with advanced can...   
6   DESTINY-Gastric03 will investigate the safety,...   
7   Recently, cytokine polymorphisms are considere...   
8   To compare the symptoms of patients who have a...   
9   With advances in chemotherapy for gastric canc...   
10  Although advances in chemotherapy have improve...   
11  Phase I Part :\n\nConfirm the safety of GAIA-1...   
12  This study is an open label phase 2 study to e...   
13  This study will assess the efficacy, safety, o...   
14  The main objectives of this study are to evalu...   
15  This study is being done to find out if zanida...   

                                    Japanes Locations  \
0                                        Chiba, Tokyo   
1   Chiba, Fukuoka, Gifu, Kumamoto, Kyoto, Nagasak...   
2   Kashiwa, Nagoya, Osakasayama, Suita, Yokohama, ku   
3                               Sapporo, gun, ku, shi   
4                                             ku, shi   
5                                         Kashiwa, ku   
6                               Kashiwa, gun, ku, shi   
7              

In [14]:
df.to_csv('./65yerProstateCancer.csv')